# Data exploration 

---

Group name: D

---


## Introduction

Der Datensatz enthält knapp 3 Millionen russische Troll-Tweets, die zwischen Februar 2012 und Mai 2018 veröffentlicht wurden.  
*Da der ursprüngliche Datensatz sehr umfangreich ist, wird im Folgenden nur ein Ausschnitt von knapp 5.000 Tweets analysiert.*

## Setup

In [27]:
import pandas as pd
import datetime as dt
import altair as alt

alt.data_transformers.disable_max_rows()

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

## Data

## Import data

In [50]:
df = pd.read_csv('../data/external/data2.csv')

### Data structure

In [ ]:
df

In [ ]:
df.info()

Der Datensatz enthält sehr viele Spalten, von denen jedoch nur ein Bruchteil für die folgende Datenanalyse benötigt wird.  
Außerdem sind manche Spalten nicht richtig formatiert (z.B. publish_date als object, obwohl hier das Format datetime richtig wäre).

### Data corrections

Löschen nicht benötigter Spalten

In [51]:
df.drop(df.columns[[0, 1, 2, 3, 5, 9, 10, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23]], axis=1, inplace=True)

Spalte "publish_date" in das "datetime"-Format umwandeln

In [52]:
df['publish_date'] = pd.to_datetime(df['publish_date'], format='%m/%d/%Y %H:%M')

df.info()

Das DataFrame ist nun kleiner und übersichtlicher. Zudem ist die Spalte "publish_date" korrekt formatiert.

## Exploratory data analysis

### Häufigste Länder

Die Tweets wurden aus verschiedenen Ländern gesendet. Welche Länder sind dabei und wir häufig wurde aus ihnen getweetet?  
Mit dem Land als einzige kategoriale Variable kann ein Donut-Diagramm die Verhältnisse gut darstellen.

In [63]:
chart_region = alt.Chart(df.dropna()).mark_arc(innerRadius=50).encode(
    theta=alt.Theta("count(region)", type="quantitative"),
    color=alt.Color("region", type="nominal", title='Länder'),
    tooltip=(
            alt.Tooltip("region")
    )
).properties(
    title='Anteil der verschiedenen Länder',
    width=400,
    height=300
)

chart_region.configure_title(
    fontSize=16,
    font='Arial',
    color='black',
    anchor='middle'
)

alt.Chart(...)

### Häufigste Sprachen

Die Tweets wurden aus verschiedenen Ländern gesendet. Aber welche Sprachen sind besonders stark vertreten?  
Hier ist die einzige kategoriale Variable die Sprache. Erneut haben wir uns für ein Donut-Diagramm entschieden.

In [64]:
chart_language = alt.Chart(df.dropna()).mark_arc(innerRadius=50).encode(
    theta=alt.Theta("count(language)", type="quantitative"),
    color=alt.Color("language", type="nominal", title='Sprachen'),
    tooltip=(
        alt.Tooltip("language")
    )
).properties(
    title='Anteil der verschiedenen Sprachen',
    width=400,
    height=300
)

chart_language.configure_title(
    fontSize=16,
    font='Arial',
    color='black',
    anchor='middle'
)

alt.Chart(...)

### Followerverteilung

Wie groß ist das Publikum der Troll-Accounts? Gibt es Accounts mit besonders vielen Followern?  
Die Anzahl der Follower ist eine einzige numerische Variable, die wir diesmal als Balkendiagramm darstellen.

In [66]:
chart_followers = alt.Chart(df).mark_bar().encode(
  x=alt.X('author',
    title="Account-Name",
    sort="-y"
  ),
  y=alt.Y('max(followers)',
    title="Anzahl Follower"
  ),
  color=alt.Color("author",
    type="nominal",
    title='Account',
    legend=None),
  tooltip=(
        alt.Tooltip("max(followers)", title="Follower")
  )
).properties(
    title='Accounts mit den meisten Followern',
    width=800,
    height=300,
)

chart_followers.configure_title(
    fontSize=16,
    font='Arial',
    color='black',
    anchor='middle'
)

alt.Chart(...)

### Posts nach Datum

Gibt es Zeiträume, in denen die Troll-Konten besonders aktiv waren? Dies lässt sich mit der Anzahl der Tweets pro Tag erkennen.

Beim Datum und der Anzahl der Tweets pro Tag handelt sich um zwei numerische Variablen. Diese stellen wir als Liniendiagramm dar.

Die Anzahl der Posts soll im Intervall von je einem Tag angezeigt werden.
Daher wird eine weitere Spalte "date" erstellt, die nur das Datum, nicht jedoch die Uhrzeit enthält:

In [68]:
df['date'] = pd.to_datetime(df['publish_date'].dt.date)

In [69]:
chart_time = alt.Chart(df).mark_line().encode(
    x=alt.X("date",
        title="Datum"
    ),
    y=alt.Y("count(date)",
        title="Anzahl der Tweets"
    ),
    tooltip=(
        alt.Tooltip("count(date)", title="Anzahl der Tweets")
    )
).properties(
    title='Anzahl der Tweets pro Tag',
    width=800,
    height=300
)

chart_time.configure_title(
    fontSize=16,
    font='Arial',
    color='black',
    anchor='middle'
)

alt.Chart(...)

### Posts nach Wochentag und Uhrzeit

Zu welchen Wochentagen und Uhrzeiten waren die Konten besonders aktiv?  
Dazu benötigen wir drei Werte: Den Wochentag, die Uhrzeit (der Einfachheit halber nur die Stunde) und die Anzahl der Tweets pro Wochentag udn Uhrzeit.  
Die Anzahl der Tweets und die Uhrzeit sind numerische Variablen, der Wochentag ist jedoch eine kategoriale Variable. Diese Kombination stellen wir in einer Heatmap dar.

Zunächst werden zwei weitere Spalten erstellt: Die Spalte "hour" enthält die Stunde der Veröffentlichung eines Tweets, und die Spalte "weekday" den Wochentag.

In [60]:
df['hour'] = df['publish_date'].dt.hour
df['weekday'] = df['publish_date'].dt.weekday

Die Wochentage sind noch als Wert zwischen 0 und 6 gespeichert (0 = Montag, ..., 6 = Sonntag).
Daher wird eine weitere Spalte "weekday_name" hinzugefügt, die die Abkürzung der Wochentage enthält:

In [61]:
weekday_names = ["Mo", "Di", "Mi", "Do", "Fr", "Sa", "So"]
df['weekday_name'] = df['weekday'].replace(range(7), weekday_names)

In [62]:
heatmap = alt.Chart(df).mark_rect().encode(
    x=alt.X("hour",
        title="Uhrzeit"
    ),
    y=alt.Y('weekday_name',
            title="Wochentag",
            type='nominal',
            sort=weekday_names
           ),
    color=alt.Color("count(weekday_name)",
    legend=None),
    tooltip=(
        alt.Tooltip("count(weekday_name)", title="Anzahl der Tweets")
    )
).properties(
    title='Tweets nach Wochentag und Uhrzeit',
    width=1000,
    height=300
)

heatmap.configure_title(
    fontSize=16,
    font='Arial',
    color='black',
    anchor='middle'
)

alt.Chart(...)